# Notebook para valoração do uso da flexibilidade de hidrelétricas através da análise do custo de soluções alternativas

Globalmente, a política de implementação de fontes renováveis tem se concentrado, principalmente, na expansão da capacidade instalada, enquanto questões operacionais, como a necessidade de flexibilidade para manter a estabilidade do sistema, bem como regulamentações e procedimentos de rede atualizados para aprimorar o controle do sistema de energia, foram frequentemente negligenciados. No entanto, atualmente, um número crescente de países está voltando sua atenção para as consequências dos altos níveis de participação de fontes de energia não convencionais no funcionamento adequado do sistema elétrico e nos mecanismos de integração dessas fontes à rede.

As usinas hidrelétricas são muito eficientes em fornecer serviços ancilares à rede elétrica, graças a sua flexibilidade. Especificamente, elas desempenham um papel crucial no controle de potência ativa e da frequência. Além disso, as usinas hidrelétricas com reservatório têm a capacidade de oferecer uma ampla gama de serviços energéticos, como geração de energia de base e de pico, bem como armazenamento de energia. Além disso, essas usinas podem desempenhar um papel importante na regulação de outras fontes de energia, com custos variáveis muito baixos.

Neste contexto de crescente uso de fontes de energia não despachável, cada vez mais as usinas hidrelétricas vão ser demandadas a fornecer serviços ancilares e de flexibilidade. É de fundamental importância a valoração destes serviços de maneira a incentivar o desenvolvimento de capacidade para os mesmos aumentando a eficiência do uso dos recursos hídricos. Desta maneira o presente trabalho visa contribuir para estimar o valor de tal serviço à sociedade através do cálculo do custo de soluções alternativas seguindo o conceito de BATNA (do inglês, *Best Alternative To a Negotiated Agreement*)  introduzido no método de negociação de Havard.

Este notebook foi feito visando a valoração do custo da flexibilidade energética de um país de consumo equivalente ao Brasil. Para isso, foram determinados dois cenárioas alternativos para suprir a flexibilidade requerida pela demanda brasileira. Imagina-se, primeiramente, um cenário com turbinas à gás, e um cenário com turbinas à gás em conjunto com baterias. Vale lembrar que para estas turbinas, foram verificados o Custo capital e os Custos de operação e manutenção; e que estes são divididos em fixos e variáveis.

Com base nesses custos e com um uma estimativa do valor de MWh usados para suprir a flexibilidade vamos alcançar um o custo, em US$/MWh flexível, associado a prover a flexibilidade sem o uso de plantas hidroelétricas, e, com base no método BATNA, alcançamos o valor da flexibilidade.

Para facilitar a utilização do especialista, o notebook está dividido em seções.

# Importação de Bibliotecas

Esta seção está organizada para a coleta de dados e definição de variáveis. É importante rodar todas estas células para que os dados dos resultados sejam encontrados sem erro de compilação. Esta seção está organizada em:

1 - Inserção de bibliotecas;

2 - Aperfeiçoamento da interface para o usuário;

3 - Definição de constantes utilizadas durante o código, desde turbinas até o vetor de demanda energética;

4 - Apresentação de gráficos mencionando os valores médios e reais da demanda brasileira.


Uma vez mencionada a organização, as três seguintes células de código serão para a declaração de variáveis no sistema do Google Colab (Notebook). Nota-se que a primeira célula é a mais demorada para ser carregada e o tempo máximo é de 2 minutos.

Aqui são instaladas todas as bibliotecas necessárias para a execução do código. Para saber mais sobre as bibliotecas utilizadas e suas versões, acesse o arquivo [requirements.txt](requirements.txt).

Obs.: A célula pode demorar até 2 minutos para rodar apenas na primeira vez que for executada.

In [1]:
%pip install -r requirements.txt -q

Note: you may need to restart the kernel to use updated packages.


In [2]:
import pandas as pd
# Pandas: Análise e manipulação de dados. Facilita operações como seleção, substituição, e agregação de dados em estruturas como DataFrames.

import numpy as np
# NumPy: Computação científica e manipulação de arrays. Fornece suporte a arrays e matrizes multidimensionais, além de uma coleção de funções matemáticas para operar nessas estruturas.

from matplotlib.colors import to_rgb, to_hex
# Matplotlib Colors: Submódulo de Matplotlib focado na conversão e manipulação de cores. to_rgb e to_hex permitem converter cores entre diferentes formatos.

from amortization.schedule import amortization_schedule
# Amortization Schedule: Utilizado para calcular a amortização de empréstimos ou hipotecas. Gera um cronograma detalhado de pagamentos, mostrando quanto de cada pagamento é destinado ao principal e aos juros.

import plotly.graph_objects as go
# Plotly: Biblioteca para criação de gráficos interativos e visualizações de dados em Python. Graph Objects (go) é um módulo que permite a construção detalhada de tipos de gráficos como linhas, barras, bolhas, mapas, entre outros, com alta interatividade e customização.

from IPython.display import display, HTML
# IPython Display: Ferramentas para a exibição rica de outputs em notebooks Jupyter/IPython. Permite exibir HTML, imagens, vídeos, e outros tipos de conteúdo de forma mais interativa e visualmente atraente.

from types import SimpleNamespace
# Types SimpleNamespace: Facilita a criação de objetos com atributos dinamicamente adicionáveis. Útil para quando se precisa de uma estrutura simples, similar a um dicionário, mas acessível via atributos.

from typing import Dict, List, Tuple

import sys


# Utilitários (pacotes do Python para formatação)

Esta seção inclui códigos auxiliares projetados para melhorar a formatação de textos e a apresentação de dados de forma mais amigável. Estes códigos não são essenciais para compreender os cálculos ou conceitos principais, portanto, é recomendável manter a célula que os contém oculta.

Um resumo das funções de formatação disponíveis:

- **Headers**: Especifica os títulos usados no formulário de definição de constantes.
- **VALORES_INICIAIS**: Estabelece as variáveis iniciais usadas no formulário de definição de constantes.
- **Gerador_Grafico_Furnas**: Define a aparência dos gráficos interativos.
- **Formulario_Furnas**: Configura o comportamento do formulário interativo.
- **Gerenciador_Constantes**: Administra a modificação das constantes definidas por meio do formulário.
- **print_bonito**: Uma função destinada a exibir dados de forma visualmente atraente, utilizando diferentes cores.

Estas ferramentas são projetadas para simplificar a visualização e interação com os dados, mas não são necessárias para entender os conceitos ou cálculos fundamentais tratados no documento.

Execute todas as células apertando o botão abaixo.

↓

In [3]:
sys.path.append('src/modules')

from src.modules.Form import Formulario_Furnas
from src.modules.Graficos import Gerador_Grafico_Furnas

# Esta função serve para mostrar os resultados de cada célula de forma mais amigável,
# afim de que o usuário tenha maior facilidade de entender os resultados.
def print_bonito(string1, dado, unidade="", string2="", comentario=""):
    html = f"""
      <p style="font-size:larger">{string1}
      <span style="color: #D5B60A;">{dado} <span style="font-size:15px">{unidade}</span> </span>
      <span>{string2}</span>
      <span style="color: #6e6e6e;">{comentario}</span>
      </h4>
      """

    display(HTML(html))

def adicionar_ponto(j: int, numero: str) -> bool:
    """
    Avalia se, para um dado número e uma dada posição, deve ser colocado o separador de milhar.

    Parâmetros
    ----------
    - j: Valor inteiro representado a posição no vetor.
    - numero: Parte inteira do numeral no formato de uma string.

    Retornos
    --------
    - Valor lógico indicando se deve ter separador de milhar
    """
    return (j+1) % 3 == 0 and j > 0 and (j+1) < len(numero) and len(numero) > 3

def formatar_numero(numero: float) -> str:
    """
    Recebe um número real e o formata com os separadores decimal e de milhar.

    Parâmetros
    ----------
    - numero: Número real que se deseja formatar.

    Retornos
    --------
    - numero_formatado: String com o número formatado.
    """
    parte_inteira = str(numero).split('.')[0][::-1]
    numero_inteiro_formatado = ''.join([num + '.' if adicionar_ponto(j, parte_inteira) else num for j, num in enumerate(parte_inteira)])[::-1]
    numero_formatado = numero_inteiro_formatado + ',' + str(numero).split('.')[1]
    return numero_formatado

# Define o formato de apresentação dos número reais no pandas
pd.set_option('display.float_format', lambda x: formatar_numero('%.2f' % x))

# Demanda Energética

O formulário a ser apresentado abaixo apresenta uma sugestão de dados padrão, coletados dos sites e PDFs mencionados. Estes valores foram coletados em sites do governo norte-americano e da General Electric. Caso o usuário deseje modificar os valores apresentados, ele poderá escolher a opção "Usar Dados Personalizados" no botão gerado pelo resultado do processamento abaixo.

Este botão mostrará dados como: taxa de juros utilizada para fazer a amortização do pagamento, dados sobre cada uma das turbinas e preço do gás natural.

Caso o usuário deseje utilizar os dados personalizados, este deverá apertar o botão de "Enviar" ao final do formulário para a validação dos novos dados. Também encontra-se, no final do formulário de dados personalizados, dois botões, um para a exportação e outro para o carrgamento de dados no formato ".CSV".

A célula de código seguinte será importante para transformar os valores encontrados no formulário inicial em valores do programa.

**Observação:** todas as mudanças no formulário serão temporárias e serão desfeitas ao rodar novamente o notebook. Caso deseje alterar permanentemente os valores iniciais, basta alterar a classe [Valores_Iniciais](#constantes) presete na seção `Utilitários`.

In [4]:
formulario = Formulario_Furnas(is_colab=False)
formulario.exibir_formulario()

Dropdown(description='Escolha:', options=('Usar Dados Padrão', 'Usar Dados Personalizados'), value='Usar Dados…

In [5]:
# Aqui são recuperadas todas as constantes definidas pelo formulário
# Para utilizar o valor armazenado, basta digitar `c.nome_da_variavel`
c = formulario.recuperar_valores()

Processamento dos dados do ano escolhido e geração do gráfico da demanda horária de potência no ano escolhido.

In [6]:
# Definição da variável que lerá o excel
# A variável lerá o arquivo Excel dentro da pasta "content" do projeto
try:
  df = pd.read_excel("src/content/CURVA_CARGA_2022.xlsx")
  df.dropna(inplace = True)
except:
  raise ValueError("Por favor, envie um arquivo Excel na célula acima.")

def processar_dados_energia(df: pd.DataFrame) -> tuple[pd.Series, list, list, list, list]:
    """
    Processa os dados de energia horária de diferentes regiões a partir de um DataFrame.

    :param df: DataFrame contendo os dados de energia e tempo.
    :return: Tupla contendo o vetor de tempo e as listas de energia horária para cada região.
    """
    energia_horaria_N = [0] * len(df)
    energia_horaria_NE = [0] * len(df)
    energia_horaria_S = [0] * len(df)
    energia_horaria_SE = [0] * len(df)
    tempo = [0] * len(df)

    # Organizando a informação colhida no arquivo Excel
    for i in range(len(df)):
        if df.iloc[i, 0] == "N":
            energia_horaria_N[i] = df.iloc[i, 3]
            tempo[i] = df.iloc[i, 2]
        if df.iloc[i, 0] == "NE":
            energia_horaria_NE[i] = df.iloc[i, 3]
        if df.iloc[i, 0] == "S":
            energia_horaria_S[i] = df.iloc[i, 3]
        if df.iloc[i, 0] == "SE":
            energia_horaria_SE[i] = df.iloc[i, 3]

    return tempo, energia_horaria_N, energia_horaria_NE, energia_horaria_S, energia_horaria_SE

def criar_serie_temporal(dados: list, inicio: int, passo: int = 4) -> pd.Series:
    """
    Função para criar uma série temporal reduzida.

    :param dados: lista ou série original de dados.
    :param inicio: índice inicial para começar a seleção.
    :param passo: passo para seleção dos elementos. Padrão é 4.
    :return: pd.Series com elementos selecionados.
    """
    selecionados = []
    for i in range(passo - inicio, len(dados), passo):
        selecionados.append(dados[i])

    return pd.Series(selecionados)

tempo, energia_horaria_N, energia_horaria_NE, energia_horaria_S, energia_horaria_SE = processar_dados_energia(df)

# Define o vetor de tempo para o "eixo x" do gráfico.
tempo_ajustado = criar_serie_temporal(tempo, inicio=0)
# Coleta os dados dos consumos de energia da região Norte.
energia_horaria_n_ajustada = criar_serie_temporal(energia_horaria_N, inicio=0)
# Coleta os dados dos consumos de energia da região Nordeste.
energia_horaria_ne_ajustada = criar_serie_temporal(energia_horaria_NE, inicio=3)
# Coleta os dados dos consumos de energia da região Sul.
energia_horaria_s_ajustada = criar_serie_temporal(energia_horaria_S, inicio=2)
# Coleta os dados dos consumos de energia da região Sudeste.
energia_horaria_se_ajustada = criar_serie_temporal(energia_horaria_SE, inicio=1)

energia_horaria_total = energia_horaria_n_ajustada + energia_horaria_ne_ajustada + energia_horaria_s_ajustada + energia_horaria_se_ajustada
energia_horaria_total.iloc[-1] = np.mean(energia_horaria_total)

grafico_consumo_energia = Gerador_Grafico_Furnas("demanda-sem-media-movel")

# Figura do gráfico "Consumo de energia x hora" em 1 ano.
fig = grafico_consumo_energia.grafico_interativo_linha(tempo_ajustado, energia_horaria_total, "Tempo (h)", "Potência (MW)", "Variação da Demanda Energética")

# Botão para exportar gráfico no formato PDF
grafico_consumo_energia.botao_exportar_pdf()

print("\n\nOBS.: Para baixar arquivos pode ser necessário desativar ADBlockers na página.")
print("\nO gráfico suporta zoom e seleção de áreas para visualização mais detalhada.")


Button(description='Exportar para PDF', style=ButtonStyle())



OBS.: Para baixar arquivos pode ser necessário desativar ADBlockers na página.

O gráfico suporta zoom e seleção de áreas para visualização mais detalhada.


Os gráficos interativos permitem zoom, foco em segmentos específicos, ocultação de curvas e exportação em PDF ou PNG para uma análise e compartilhamento facilitados.

Esta parte concentra-se a média móvel do ano de 2022 em 7 dias.

In [7]:
# Lista para armazenar a demanda sem aplicação da média móvel
demanda_sem_media_movel = []
# Lista para armazenar a demanda com aplicação da média móvel de 7 dias
demanda_com_media_movel = []
# Número de dias considerados na média móvel multiplicado pelas 24 horas do dia
numero_horas_semana = 7 * 24  # sete dias, 24 horas cada
i = 0

# Calculando a média móvel da demanda
while i < len(energia_horaria_total) - numero_horas_semana + 1:
    # Selecionando a janela de tempo atual para cálculo da média
    janela_atual = energia_horaria_total[i : i + numero_horas_semana]

    # Calculando a média da janela de tempo atual
    media_janela_atual = sum(janela_atual) / numero_horas_semana

    # Armazenando a média calculada na lista de demanda com média móvel
    demanda_com_media_movel.append(media_janela_atual)

    # Calculando a média sem ser móvel para cada posição e armazenando na respectiva lista
    demanda_sem_media_movel.append(np.average(energia_horaria_total))

    # Deslocando a janela de tempo uma posição para a direita
    i += 1

# Preenchendo a lista de demanda sem média móvel para os últimos dias
i = 0
while i < 7 * 24:
    demanda_sem_media_movel.append(np.average(energia_horaria_total))
    i += 1

gerador_grafico_demanda = Gerador_Grafico_Furnas("demanda-com-media-movel")

# Gerando um gráfico interativo com múltiplas linhas
fig = gerador_grafico_demanda.grafico_interativo_multiplas_linhas(
    tempo_ajustado,
    [energia_horaria_total[0 : 365 * 24], demanda_com_media_movel[0 : 365 * 24 - numero_horas_semana], demanda_sem_media_movel[0 : 365 * 24]],
    "Tempo (h)",
    "Demanda (MW)",
    "Variação da Demanda Energética, Média e Média Móvel de Uma Semana no Ano de 2022",
    ["Demanda Horária", "Demanda com Média Móvel de 7 dias", "Demanda Média Anual"]
)

# Adicionando um botão para exportar o gráfico em formato PDF
gerador_grafico_demanda.botao_exportar_pdf()
print("\nO gráfico suporta zoom, seleção de áreas para visualização mais detalhada e seleção de linhas para visualização individual.")


Button(description='Exportar para PDF', style=ButtonStyle())


O gráfico suporta zoom, seleção de áreas para visualização mais detalhada e seleção de linhas para visualização individual.


# Flexibilidade Energética

Nesta parte calcula-se a média de consumo energético em um ano, verifica-se também o consumo máximo e o mínimo de consumo de energia no ano (considerando o intervalo de 1 hora).

A energia necessária pode ser encontrada pela seguinte relação:

$$
\text{Energia necessária} = \text{Valor máximo anual} - \text{Valor médio anual}
$$


Na célula abaixo, definimos os valores de consumo máximo e mínimo, bem como a média de consumo de energia no ano a partir dos dados de demanda energética do arquivo Excel carregado anteriormente.

Para utilizar valores personalizados, basta alterar os valores das variáveis `consumo_maximo`, `consumo_minimo` e `consumo_medio` na célula abaixo.

In [8]:
consumo_medio = np.average(energia_horaria_total) # média do ano
consumo_maximo =(np.max(energia_horaria_total)) # máximo do ano
consumo_minimo =(np.min(energia_horaria_total)) # mínimo do ano

energia_necessaria = consumo_maximo - consumo_medio

print_bonito("Média do ano:", formatar_numero(round(consumo_medio, 2)), "MW.")
print_bonito("Máximo do ano:", formatar_numero(round(consumo_maximo, 2)), "MW.")
print_bonito("Mínimo do ano:", formatar_numero(round(consumo_minimo, 2)), "MW.")
print_bonito("Quantos MW instalados estão parados em média:", formatar_numero(round(energia_necessaria, 2)), "MW.")

In [9]:
def media_movel(array_entrada: List[float], tamanho_janela: int) -> List[float]:
    """
    Calcula a média móvel de um array de entrada.

    :param array_entrada: Lista de valores numéricos de entrada.
    :param tamanho_janela: Tamanho da janela para calcular a média móvel.
    :return: Uma lista contendo os valores da média móvel.
    """
    array_media_movel = []
    num_elementos = len(array_entrada)

    for i in range(num_elementos):
        indice_inicio = max(0, i - tamanho_janela + 1)
        indice_fim = i + 1
        janela = array_entrada[indice_inicio:indice_fim]
        media = sum(janela) / len(janela)
        array_media_movel.append(media)

    return array_media_movel

def calcular_diferenca(array1: List[float], array2: List[float], tamanho_janela: int) -> Tuple[List[float], float, int]:
    """
    Calcula a diferença entre dois arrays em janelas especificadas e encontra a diferença máxima.

    :param array1: Primeiro array de valores numéricos.
    :param array2: Segundo array de valores numéricos.
    :param tamanho_janela: Tamanho da janela para calcular as diferenças.
    :return: Uma tupla contendo a lista de diferenças, a maior diferença e o índice da maior diferença.
    """
    diferencas = []
    diferenca_maxima = float("-inf")
    indice_diferenca_maxima = None

    array1_np = np.array(array1)
    array2_np = np.array(array2)

    for i in range(0, len(array1_np), tamanho_janela):
        janela1 = array1_np[max(0, i - int(tamanho_janela/2)) : i + int(tamanho_janela/2)]
        janela2 = array2_np[max(0, i - int(tamanho_janela/2)) : i + int(tamanho_janela/2)]

        mascara = janela1 > janela2
        diff = np.sum(janela1[mascara] - janela2[mascara])
        diferencas.append(diff)

        if diff > diferenca_maxima:
            diferenca_maxima = diff
            indice_diferenca_maxima = i

    return diferencas, diferenca_maxima, indice_diferenca_maxima


tamanho_teste = 15 * 24
MA_array = media_movel(energia_horaria_total, tamanho_teste)

aux_1 = energia_horaria_total[int(tamanho_teste):365*24 - int(np.ceil(0.5 * tamanho_teste))]
aux_2 = MA_array[int(np.ceil(1.5*tamanho_teste)):365*24]

array_teste, max_energia, indice_max_energia = calcular_diferenca(aux_1, aux_2, tamanho_teste)

gerador_grafico_maior_demanda = Gerador_Grafico_Furnas("Dia de maior consumo no ano")

fig = gerador_grafico_maior_demanda.grafico_interativo_multiplas_linhas(
    tempo_ajustado[12:],
    [aux_1, aux_2],
    "Tempo (h)",
    "Demanda (MW)",
    "Demanda de Energia durante 2022 e sua Média Móvel de 15 dias",
    ["Demanda Hora a Hora", "Média Móvel de 15 dias"]
)

print("Figura 1 - Demanda sem média móvel [MW]")

gerador_grafico_maior_demanda.botao_exportar_pdf()


Figura 1 - Demanda sem média móvel [MW]


Button(description='Exportar para PDF', style=ButtonStyle())

## Análise Econômica da Flexibilidade em Geração de Energia Termelétrica

Com base em dados extraídos de artigos científicos, foram definidas as capacidades de geração de energia em Megawatts (MW) para diferentes tipos de turbinas termelétricas: CCGT (Combined Cycle Gas Turbine) e LFGT (Landfill Gas Turbine) com 450 MW; AeroGT (Aeroderivative Gas Turbine) com 53 MW; e SteamGT (Steam Gas Turbine) com 300 MW. Utilizando estas constantes, foi possível calcular o número necessário de turbinas e quantas permaneceriam inativas em algum momento.

O custo total mensal é determinado pela soma do custo de instalação com o custo mensal de manutenção. A partir desses dados, calcula-se o custo da flexibilidade, que reflete o impacto econômico sobre o fornecimento total de energia.

O consumo de energia pode ser dividido em duas partes principais:
1. **Consumo de Base**: Representado pelo valor mínimo de consumo ao longo do ano.
2. **Consumo Flexível**: Que oscila ao longo do tempo, calculado pela diferença entre o consumo médio e o consumo mínimo.

Apenas o consumo flexível demanda flexibilidade na geração, permitindo assim determinar o custo de capital por MegaWatt flexível (US$/MWh Flexível).

### Fórmulas

- **Custo por MWh - Custo de Flexibilidade (US$/MWh)**:

$$
\text{Custo por MWh} = \frac{\text{Custo Mensal Total}}{\text{Média Anual} \times 30 \times 24}
$$

- **Custo de Capital por MWh Flexível (US$/MWh)**:

$$
\text{Custo MWh Flexível} = \frac{\text{Custo Mensal Total}}{(\text{Média Anual} - \text{Consumo Mínimo}) \times 30 \times 24}
$$

Este cálculo destina-se a refletir o impacto econômico sobre o fornecimento total de energia, focando especialmente na parte do consumo que requer flexibilidade.

In [10]:
def calcular_custos_tecnologia(energia_necessaria: float, potencia_tecnologia: float, custo_capital: float, custo_om: float, meses: int = c.TEMPO_PAGAR_TURBINA, taxa_juros: float = c.TAXA_DE_JUROS) -> Dict[str, float]:
    """
    Calcula os custos para uma determinada tecnologia ao longo de um período especificado.

    :param energia_necessaria: Energia necessária a ser gerada em MWh.
    :param potencia_tecnologia: Potência da tecnologia em uso em MW.
    :param custo_capital: Custo de capital inicial por unidade de potência em US$/MW.
    :param custo_om: Custo de operação e manutenção anual por unidade de potência em US$/MW/ano.
    :param meses: Duração do financiamento em meses.
    :param taxa_juros: Taxa de juros anual.
    :return: Dicionário com os custos calculados, incluindo o número de unidades necessárias, custo total do capital, pagamento mensal, custo de operação e manutenção mensal, custo mensal total, custo por MWh, e custo por MWh flexível.
    """
    n_unidades = int(np.ceil(energia_necessaria / potencia_tecnologia))
    custo_capital_total = n_unidades * custo_capital * 1000 * potencia_tecnologia
    custo_om_anual = n_unidades * potencia_tecnologia * custo_om

    meses = int(meses)

    # Calcular pagamento mensal amortizado
    pagamento_mensal = None
    for _, amount, _, _, _ in amortization_schedule(custo_capital_total, taxa_juros, meses):
        pagamento_mensal = amount
    if pagamento_mensal is None:
        raise ValueError("Falha no cálculo da tabela de amortização.")

    custo_mensal_total = custo_om_anual / 12 + pagamento_mensal
    custo_por_mwh = custo_mensal_total / (consumo_medio * 30 * 24)
    custo_mwh_flexivel = custo_mensal_total / ((consumo_medio - consumo_minimo) * 30 * 24)

    return {
        "n_unidades": n_unidades,
        "custo_capital_bilhao": round(custo_capital_total / 1e9, 3),
        "pagamento_mensal_milhao": round(pagamento_mensal / 1e6, 3),
        "custo_om_mensal_milhao": round(custo_om_anual / 12 / 1e6, 3),
        "custo_mensal_total_milhao": round(custo_mensal_total / 1e6, 2),
        "custo_por_mwh": round(custo_por_mwh, 2),
        "custo_mwh_flexivel" : round(custo_mwh_flexivel, 2)
    }

def mostrar_tabela_custos(custos: Dict[str, float], tecnologia: str) -> None:
    """
    Exibe uma tabela HTML com os custos calculados para uma tecnologia específica.

    :param custos: Dicionário contendo os custos calculados para a tecnologia.
    :param tecnologia: Nome da tecnologia para a qual os custos são calculados.
    """
    html = f"""
    <table>
    <h3 style="color:#D5B60A">Custos para {tecnologia}</h3>
    <br>
    <tr><th>Descrição</th><th>Valor</th></tr>
    <tr><td>Valor 1 {tecnologia}</td><td>US$ {formatar_numero(custos['custo_capital_bilhao'])} bilhões</td></tr>
    <tr><td>Número de {tecnologia} paradas, em média</td><td>{custos['n_unidades']}</td></tr>
    <tr><td>Custo Capital da flexibilidade mensal para {tecnologia}</td><td>US$ {formatar_numero(custos['pagamento_mensal_milhao'])} milhões</td></tr>
    <tr><td>Custo de Manutenção da flexibilidade mensal para {tecnologia}s</td><td>US$ {formatar_numero(custos['custo_om_mensal_milhao'])} milhões</td></tr>
    <tr><td>Custo total mensal para {tecnologia} - soma dos últimos dois de cima</td><td>US$ {formatar_numero(custos['custo_mensal_total_milhao'])} milhoões</td></tr>
    <tr><td>Custo flexibilidade para {tecnologia}</td><td>US$ {formatar_numero(custos['custo_por_mwh'])} /MWh</td></tr>
    <tr><td>Custo MWh flexível {tecnologia}</td><td>US$ {formatar_numero(custos['custo_mwh_flexivel'])} /MWh</td></tr>
    </table>
    """
    display(HTML(html))

# CCGT
ccgt_custos = calcular_custos_tecnologia(
    energia_necessaria, c.CCGT_POTENCIA, c.CCGT_CUSTO_TOTAL, c.CCGT_CUSTO_OM)

mostrar_tabela_custos(ccgt_custos, "CCGT")

# AeroGT

aerogt_custos = calcular_custos_tecnologia(
    energia_necessaria, c.AERO_POTENCIA, c.AERO_CUSTO_TOTAL, c.AERO_CUSTO_OM)

mostrar_tabela_custos(aerogt_custos, "AeroGT")

# HeavyDuty

heavyduty_custos = calcular_custos_tecnologia(
    energia_necessaria, c.HEAVY_DUTY_POTENCIA, c.HEAVY_DUTY_CUSTO_TOTAL, c.HEAVY_DUTY_CUSTO_OM)

mostrar_tabela_custos(heavyduty_custos, "HeavyDuty")


# Armazenamento

Este script Python foi desenvolvido para calcular diferentes métricas relacionadas ao armazenamento de energia, com foco em sistemas de baterias.


A função `calcular_armazenamento` é responsável por calcular diversas métricas diárias relacionadas ao armazenamento de energia. Ela recebe um índice de início como parâmetro, presumivelmente representando o início de um novo dia.

Dentro da função:

- **Amplitude Diária**: Calcula a amplitude da energia para cada hora do dia e a armazena em uma lista.
- **Média Diária**: Calcula a média da amplitude diária.
- **Throughput**: Calcula o throughput, definido como a diferença entre o máximo de energia e a média diária.
- **Integral Acima e Abaixo**: Calcula a integral das diferenças entre cada ponto de energia e a média diária, para valores acima e abaixo da média, respectivamente.

A função retorna uma tupla contendo as integrais acima e abaixo, o throughput, a média diária e o índice de início.



In [11]:
def calcular_armazenamento(indice_inicio: int, energia_horaria_total: List[float]) -> Tuple[float, float, float, float, int]:
    """
    Calcula os parâmetros de armazenamento de energia baseado na energia horária total.

    :param indice_inicio: O índice de início da janela de 24 horas na lista de energia horária total.
    :param energia_horaria_total: Lista de valores de energia total por hora.
    :return: Uma tupla contendo a soma da energia acima da média, a soma da energia abaixo da média,
             o throughput (diferença entre o máximo diário e a média diária), a média diária de energia,
             e o índice de início.
    """
    amplitude_dia = [energia_horaria_total[i] for i in range(indice_inicio, min(indice_inicio + 24, len(energia_horaria_total)))]
    media_dia = np.mean(amplitude_dia)
    throughput = np.max(amplitude_dia) - media_dia

    integral_acima = np.sum([max(0, i - media_dia) for i in amplitude_dia])
    integral_abaixo = np.sum([max(0, media_dia - i) for i in amplitude_dia])

    return (integral_acima, integral_abaixo, throughput, media_dia, indice_inicio)

def exibir_armazenamento(valor_max_armazenamento: float, max_throughput: float, max_termo_bateria: float) -> None:
    """
    Exibe os valores máximos de armazenamento, throughput e termo de bateria usando HTML.

    :param valor_max_armazenamento: O valor máximo de energia armazenada acima da curva de demanda.
    :param max_throughput: O valor máximo de throughput.
    :param max_termo_bateria: O valor máximo do termo da bateria.
    """

    html = f"""
    <ul style="font-size: larger;">
        <li>Acima da curva: <span style="color: #D5B60A;">{formatar_numero(round(valor_max_armazenamento, 2))} MWh</span></li>
        <li>Maior diferença média do máximo diário: <span style="color: #D5B60A;">{formatar_numero(round(max_throughput, 2))} MW</span></li>
        <li>Max Termo Bateria: <span style="color: #D5B60A;">{formatar_numero(round(max_termo_bateria, 2))} MW</span></li>
    </ul>
    """
    display(HTML(html))

valores_armazenamento = []
throughputs = []
medias_diarias = []

maior_throughput = -np.inf
indice_maior_throughput = 0
maior_armazenamento = -np.inf
indice_maior_armazenamento = 0

for i in range(0, len(energia_horaria_total), 24):
    resultado = calcular_armazenamento(i, energia_horaria_total)

    if resultado[0] > maior_armazenamento:
        maior_armazenamento = resultado[0]
        indice_maior_armazenamento = resultado[4]

    if resultado[2] > maior_throughput:
        maior_throughput = resultado[2]
        indice_maior_throughput = resultado[4]

    valores_armazenamento.append(resultado[0])
    throughputs.append(resultado[2])
    medias_diarias.append(resultado[3])

valor_max_armazenamento = np.max(valores_armazenamento)
max_throughput = np.max(throughputs)
max_termo_bateria = np.max(medias_diarias)

exibir_armazenamento(valor_max_armazenamento, max_throughput, max_termo_bateria)


In [12]:
dados_maior_throughput = energia_horaria_total[indice_maior_throughput:indice_maior_throughput+24]
media_dia_maior_throughput = np.mean(dados_maior_throughput)
media_anual = np.mean(energia_horaria_total)

# Gera listas de valores constantes para a média diária do dia de maior throughput e a média anual
lista_media_dia_maior_throughput = [media_dia_maior_throughput] * 24
lista_media_anual = [media_anual] * 24

# Criação e configuração do gráfico
gerador_grafico_maior_dia = Gerador_Grafico_Furnas("Gráfico do Dia com Maior Throughput")
gerador_grafico_maior_dia.grafico_interativo_multiplas_linhas(
    list(range(24)),  
    [
        dados_maior_throughput,
        lista_media_dia_maior_throughput,
        lista_media_anual
    ], 
    "Tempo (h)",
    "Potência (MW)",  
    nome_legenda=["Dia com Maior Throughput", "Média do Dia", "Média Anual"]  
)
gerador_grafico_maior_dia.botao_exportar_pdf()

Button(description='Exportar para PDF', style=ButtonStyle())

In [13]:
dados_maior_armazenamento = energia_horaria_total[indice_maior_armazenamento:indice_maior_armazenamento+24]

# Calcula a média para o dia com maior armazenamento e para o ano.
media_dia_maior_armazenamento = np.mean(dados_maior_armazenamento)

# Gera listas de valores constantes para a média do dia de maior armazenamento e a média anual.
lista_media_dia_maior_armazenamento = [media_dia_maior_armazenamento] * 24

# Criação e configuração do gráfico para o dia com maior armazenamento.
gerador_grafico_maior_armazenamento = Gerador_Grafico_Furnas("Dia com Maior Armazenamento")
gerador_grafico_maior_armazenamento.grafico_interativo_multiplas_linhas(
    list(range(24)), 
    [
        dados_maior_armazenamento,
        lista_media_dia_maior_armazenamento,
        lista_media_anual
    ],
    "Tempo (h)",
    "Potência (MW)", 
    nome_legenda=["Dia com Maior Armazenamento", "Média do Dia", "Média Anual"]  
)
gerador_grafico_maior_armazenamento.botao_exportar_pdf()

Button(description='Exportar para PDF', style=ButtonStyle())

In [14]:
def amortizacao(custo_para_amortizar: float, taxa_juros_anual: float, periodos: int):
    """
    Calcula o valor da parcela mensal para um empréstimo com base na fórmula de amortização.

    Parâmetros:
    - custo_para_amortizar: O valor total a ser amortizado.
    - taxa_juros_anual: A taxa de juros anual.
    - periodos: O número total de períodos de pagamento (em meses).

    Retorna:
    - O valor da parcela mensal.
    """
    taxa_juros_mensal = taxa_juros_anual / 12
    parcela_mensal = (custo_para_amortizar * taxa_juros_mensal) / (1 - (1 + taxa_juros_mensal) ** -periodos)
    return parcela_mensal

def calcula_custo_termoeletricas(consumo_maximo: int, energia_necessaria: int, c: SimpleNamespace) -> HTML:
    """
    Calcula e retorna uma tabela HTML com o total de usinas termelétricas paradas,
    o custo de instalação, o custo anual dessas usinas e o custo mensal da instalação,
    baseado nos parâmetros fornecidos e nos custos fixos contidos em `c`.

    :param consumo_maximo: O consumo máximo de energia.
    :param energia_necessaria: A energia necessária durante o período de análise.
    :param c: Um objeto contendo as constantes de custo e potência para as usinas Heavy Duty.

    :returns: Uma tabela HTML como string com os resultados dos cálculos.
    """
    potencia_termo = c.HEAVY_DUTY_POTENCIA
    termoeletricas_total = np.ceil(consumo_maximo/potencia_termo)
    n_paradas = np.ceil(energia_necessaria/potencia_termo)

    valor_instalacao = n_paradas * c.HEAVY_DUTY_CUSTO_TOTAL * potencia_termo  # US$

    custo_termo_paradas = c.HEAVY_DUTY_CUSTO_OM # $/MW/ano
    custo_anual_termo_paradas = n_paradas * custo_termo_paradas * potencia_termo  # US$/ano

    custo_termo_instalada = c.HEAVY_DUTY_CUSTO_TOTAL # $/MW
    custo_instalacao_termo_paradas = n_paradas * custo_termo_instalada * potencia_termo / 12 # $/mês

    custo_para_amortizar = custo_instalacao_termo_paradas * 12  # Anualizando o custo
    parcela_mensal_TD_c2 = amortizacao(custo_para_amortizar, 0.05, 12*20)

    html = f"""
    <table>
    <h3 style="color:#D5B60A">Custos para Usinas Termelétricas</h3>
    <br>
    <tr><th>Descrição</th><th>Valor</th></tr>
    <tr><td>Total de Usinas Termelétricas necessárias</td><td>{int(termoeletricas_total)}</td></tr>
    <tr><td>Número de Usinas Termelétricas Paradas</td><td>{int(n_paradas)}</td></tr>
    <tr><td>Custo de Instalação das Usinas Termelétricas Paradas</td><td>US$ {formatar_numero(round(valor_instalacao, 2))}</td></tr>
    <tr><td>Custo Anual das Usinas Termelétricas Paradas </td><td>US$ {formatar_numero(round(custo_anual_termo_paradas, 2))}</td></tr>
    <tr><td>Custo Mensal da Instalação das Usinas Termelétricas Paradas</td><td>US$ {formatar_numero(round(custo_instalacao_termo_paradas, 2))}</td></tr>
    <tr><td>Parcela Mensal para Amortização das Usinas Termelétricas Paradas</td><td>US$ {formatar_numero(round(parcela_mensal_TD_c2, 2))}</td></tr>
    </table>
    """

    return html


display(HTML(calcula_custo_termoeletricas(consumo_maximo, energia_necessaria, c)))


## Baterias

Neste segmento do projeto, objetivamos identificar a combinação ideal de baterias que atenda simultaneamente às necessidades de potência (kW) e energia (kWh) do Brasil no ano de 2022. Para alcançar este objetivo, empregamos um sistema de equações lineares que maximiza os valores de armazenamento e de transferência de energia, considerando os custos associados.

**Formulação Matemática:**

- Minimização de Custo de Armazenamento (kW):
$$\text{max storage value (kW)} = \frac{\text{custo } a }{\text{custo de } a \text{ por kW}} + \frac{\text{custo } b }{\text{custo de } b \text{ por kW}}$$

- Minimização de Custo de Transferência (kWh):
$$\text{max throughput (kWh)} = \frac{\text{custo } a }{\text{custo de } a \text{ por kWh}} + \frac{\text{custo } b }{\text{custo de } b \text{ por kWh}}$$

Por meio desta abordagem, calculamos os valores ótimos de \(custo a\) e \(custo b\) que satisfazem ambas as demandas.

Neste formulário estão definidos os valores necessários para os cálculos.

In [15]:
formulario2 = Formulario_Furnas(mode="baterias", is_colab=False)
formulario2.exibir_formulario()

Dropdown(description='Escolha:', options=('Usar Dados Padrão', 'Usar Dados Personalizados'), value='Usar Dados…

In [18]:
c2 = formulario2.recuperar_valores()

# Converter os dados para um dicionário e então para um DataFrame
dados_dict: Dict[str, float] = vars(c2)
dados_df: Dict[str, List] = {
    "bateria": [],
    "custo_por_kw": [],
    "custo_por_kwh": [],
    "vida_util": []
}

dicionario_traducao: Dict[str, str] = {
    "CHUMBO_ACIDO": "Chumbo-Ácido",
    "LI_ION": "Lítio-Íon",
    "SODIO_ENXOFRE": "Sódio-Enxofre",
    "FLUXO_OXIDACAO": "Fluxo de Oxidação",
    "SODIO_METAL": "Sódio-Metal",
    "ZINCO_CATODO": "Zinco-Cátodo Híbrido",
    "ULTRACAPACITOR": "Ultracapacitor",
}

for key, value in dados_dict.items():
    # Extrai o nome, tipo de dado (kw, kwh, vida util) e valor
    name, data_type = key.rsplit("_", 1)
    if data_type == "KW":
        dados_df["bateria"].append(dicionario_traducao[name])
        dados_df["custo_por_kw"].append(value)
    elif data_type == "KWh":
        dados_df["custo_por_kwh"].append(value)
    else:
        dados_df["vida_util"].append(value)

# Criação do DataFrame
df_baterias = pd.DataFrame(dados_df)

display(df_baterias)

bateria  custo_por_kw  custo_por_kwh  vida_util
0          Chumbo-Ácido      2.194,00         549,00       3,00
1             Lítio-Íon      1.876,00         469,00      10,00
2         Sódio-Enxofre      3.626,00         907,00      13,50
3     Fluxo de Oxidação      3.430,00         858,00      15,00
4           Sódio-Metal      3.710,00         928,00      12,50
5  Zinco-Cátodo Híbrido      2.202,00         551,00      10,00
6        Ultracapacitor        930,00      74.480,00      16,00

In [19]:
valor_max_armazenamento_baterias = valor_max_armazenamento * 1e3 # MWh para kWh
max_throughput_baterias = max_throughput * 1e3 # MW para kW

def encontrar_par_otimo(df: pd.DataFrame, valor_maximo_armazenamento: float, valor_maximo_fluxo: float) -> pd.DataFrame:
    """
    Encontra a combinação ótima de pares de baterias com base em um valor máximo de armazenamento e fluxo,
    minimizando o custo total.

    :param df: DataFrame contendo os dados das baterias.
    :param valor_maximo_armazenamento: O valor máximo de armazenamento desejado.
    :param valor_maximo_fluxo: O valor máximo de fluxo (throughput) desejado.
    :return: Um DataFrame contendo as combinações ótimas dos pares de baterias e seus respectivos custos.
    """
    resultados: List[Dict[str, float]] = []
    n: int = len(df)

    for i in range(n):
        for j in range(i + 1, n):
            bateria_a = df.iloc[i]
            bateria_b = df.iloc[j]

            try:
                coeficientes = [
                    [1/bateria_a['custo_por_kw'], 1/bateria_b['custo_por_kw']],
                    [1/bateria_a['custo_por_kwh'], 1/bateria_b['custo_por_kwh']]
                ]

                valores = [valor_maximo_armazenamento, valor_maximo_fluxo]

                solucao = np.linalg.solve(coeficientes, valores)

                if solucao[0] < 0 or solucao[1] < 0:
                    temp_a_kw = valor_maximo_armazenamento * bateria_a['custo_por_kw']
                    temp_b_kw = valor_maximo_armazenamento * bateria_b['custo_por_kw']

                    temp_a_kwh = valor_maximo_fluxo * bateria_a['custo_por_kwh']
                    temp_b_kwh = valor_maximo_fluxo * bateria_b['custo_por_kwh']

                    max_a = max([temp_a_kw, temp_a_kwh])
                    max_b = max([temp_b_kw, temp_b_kwh])

                    if max_a > max_b:
                        solucao[0] = 0
                        solucao[1] = max_b
                    else:
                        solucao[1] = 0
                        solucao[0] = max_a

                if solucao[0] >= 0 and solucao[1] >= 0:
                    resultados.append({
                        'bateria_a': bateria_a['bateria'],
                        'bateria_b': bateria_b['bateria'],
                        'custo_total_a': solucao[0],
                        'custo_total_b': solucao[1],
                        'total': solucao[0] + solucao[1]
                    })

            except np.linalg.LinAlgError:
                print(f"Erro: Matriz singular para as baterias {bateria_a['bateria']} e {bateria_b['bateria']}")
                continue
            except ZeroDivisionError:
                print(f"Erro: Divisão por zero para as baterias {bateria_a['bateria']} e {bateria_b['bateria']}")
                continue

    resultados = sorted(resultados, key=lambda x: x['total'])
    resultados_df = pd.DataFrame(resultados)
    return resultados_df

display(HTML("<h2 style='color: #D5B60A'>Combinação Ótima - Custo Total (sem amortização)</h2>"))

df_resultados = encontrar_par_otimo(df_baterias, valor_max_armazenamento_baterias, max_throughput_baterias)
display(df_resultados.head(10))  # Mostra os 10 primeiros valores

print("Custos em US$")

bateria_a          bateria_b      custo_total_a  \
0             Lítio-Íon     Ultracapacitor   7.127.755.743,04   
1          Chumbo-Ácido     Ultracapacitor   8.343.601.435,24   
2  Zinco-Cátodo Híbrido     Ultracapacitor   8.373.996.982,04   
3     Fluxo de Oxidação     Ultracapacitor  13.039.713.420,15   
4         Sódio-Enxofre     Ultracapacitor  13.784.404.317,92   
5           Sódio-Metal     Ultracapacitor  14.103.557.559,85   
6          Chumbo-Ácido          Lítio-Íon               0,00   
7             Lítio-Íon      Sódio-Enxofre 162.411.053.993,13   
8             Lítio-Íon  Fluxo de Oxidação 162.411.053.993,13   
9             Lítio-Íon        Sódio-Metal 162.411.053.993,13   

       custo_total_b              total  
0  76.979.460.219,93  84.107.215.962,97  
1  76.976.229.082,96  85.319.830.518,20  
2  76.976.240.821,91  85.350.237.803,95  
3  76.977.393.424,82  90.017.106.844,97  
4  76.977.505.143,67  90.761.909.461,59  
5  76.977.549.409,62  91.081.106.969,47  
6 162.411.053.993,13 162.411.053.993,13  
7               0,00 162.411.053.993,13  
8               0,00 162.411.053.993,13  
9               0,00 162.411.053.993,13

Custos em US$


In [20]:
def mostrar_grafico_combinacoes_otimas(df_resultados: pd.DataFrame) -> None:
    """
    Gera e exibe um gráfico de barras horizontais com as combinações ótimas de baterias
    baseado no custo total não amortizado.

    :param df_resultados: DataFrame contendo os resultados das combinações ótimas de baterias.
    """
    melhores_baterias: List[str] = []
    melhores_valores: List[float] = []

    for indice, linha in df_resultados.iterrows():
        if linha['custo_total_a'] != 0 and linha['custo_total_b'] != 0:
            melhores_baterias.append(linha['bateria_a'] + " + " + linha['bateria_b'])
            melhores_valores.append(linha['total'])
        else:
            if linha['bateria_a'] not in melhores_baterias and linha['custo_total_a'] != 0:
                melhores_baterias.append(linha['bateria_a'])
                melhores_valores.append(linha['custo_total_a'])
            if linha['bateria_b'] not in melhores_baterias and linha['custo_total_b'] != 0:
                melhores_baterias.append(linha['bateria_b'])
                melhores_valores.append(linha['custo_total_b'])

    figura = go.Figure()

    figura.add_trace(go.Bar(
        y=melhores_baterias,
        x=melhores_valores,
        name='Valor',
        orientation='h'
    ))

    figura.update_layout(
        title='Combinação Ótima de Baterias - Custo Total Não Amortizado',
        xaxis_title='Custo Total (US$)',
        yaxis_title='Bateria',
        yaxis=dict(autorange="reversed")
    )

    figura.show()

mostrar_grafico_combinacoes_otimas(df_resultados) 


**Cálculo de Parcelas Amortizadas Baseado na Vida Útil das Baterias:**

Para determinar o custo efetivo das baterias ao longo de sua vida útil, calculamos o valor das parcelas amortizadas utilizando a tabela de preços `price` para os cálculos de amortização. A fórmula aplicada é:

- **Fórmula da Parcela Amortizada:**
$$
    PMT = \frac{ \text{custo capital}  \times  \text{taxa de juros}}{ 1 - (1 + \text{taxa juros})^{\text{-vida útil}}}
$$


In [21]:
def calcular_parcela_price(C: float, taxa_juros_anual: float, anos: int) -> float:
    """
    Calcula o valor da parcela usando a fórmula da tabela Price.

    :param C: Valor presente ou montante do financiamento.
    :param taxa_juros_anual: Taxa de juros anual.
    :param anos: Duração do financiamento em anos.
    :return: O valor da parcela.
    """
    i = taxa_juros_anual / 12  # Conversão da taxa anual para mensal
    n = anos * 12  # Total de meses
    PMT = C * (i * (1 + i)**n) / ((1 + i)**n - 1)
    return PMT

def encontrar_par_otimo_com_amortizacao(df: pd.DataFrame, valor_maximo_armazenamento: float, valor_maximo_fluxo: float, taxa_juros: float) -> pd.DataFrame:
    """
    Encontra a combinação ótima de pares de baterias considerando a amortização,
    baseado em um valor máximo de armazenamento e fluxo, minimizando o custo total.

    :param df: DataFrame contendo os dados das baterias.
    :param valor_maximo_armazenamento: O valor máximo de armazenamento desejado.
    :param valor_maximo_fluxo: O valor máximo de fluxo (throughput) desejado.
    :param taxa_juros: Taxa de juros anual para cálculo da amortização.
    :return: Um DataFrame contendo as combinações ótimas dos pares de baterias e seus respectivos custos amortizados.
    """
    resultados = []
    n = len(df)

    for i in range(n):
        for j in range(i + 1, n):
            bateria_a = df.iloc[i]
            bateria_b = df.iloc[j]

            try:
                coeficientes = [
                    [1/bateria_a["custo_por_kw"], 1/bateria_b["custo_por_kw"]],
                    [1/bateria_a["custo_por_kwh"], 1/bateria_b["custo_por_kwh"]]
                ]

                valores = [valor_maximo_armazenamento, valor_maximo_fluxo]
                solucao = np.linalg.solve(coeficientes, valores)

                if solucao[0] < 0 or solucao[1] < 0:
                    temp_a_kw = valor_maximo_armazenamento * bateria_a['custo_por_kw']
                    temp_b_kw = valor_maximo_armazenamento * bateria_b['custo_por_kw']
                    temp_a_kwh = valor_maximo_fluxo * bateria_a['custo_por_kwh']
                    temp_b_kwh = valor_maximo_fluxo * bateria_b['custo_por_kwh']
                    max_a = max([temp_a_kw, temp_a_kwh])
                    max_b = max([temp_b_kw, temp_b_kwh])

                    if max_a > max_b:
                        solucao[0] = 0
                        solucao[1] = max_b
                    else:
                        solucao[1] = 0
                        solucao[0] = max_a

                if solucao[0] >= 0 and solucao[1] >= 0:
                    solucao[0] = calcular_parcela_price(solucao[0], taxa_juros, bateria_a['vida_util'])
                    solucao[1] = calcular_parcela_price(solucao[1], taxa_juros, bateria_b['vida_util'])

                    resultados.append({
                        'bateria_a': bateria_a['bateria'], 'bateria_b': bateria_b['bateria'],
                        'parcela_a': solucao[0], 'parcela_b': solucao[1], 'total': solucao[0] + solucao[1]
                    })

            except np.linalg.LinAlgError:
                print("Erro: Matriz singular para as baterias", bateria_a['bateria'], "e", bateria_b['bateria'])
                continue
            except ZeroDivisionError:
                print("Erro: Divisão por zero para as baterias", bateria_a['bateria'], "e", bateria_b['bateria'])
                continue

    resultados = sorted(resultados, key=lambda x: x['total'])
    resultados_df = pd.DataFrame(resultados)
    return resultados_df

display(HTML("<h2 style='color: #D5B60A'>Combinação Ótima - Custo da Parcela (Com Amortização)</h2>"))

df_resultados_amortizados = encontrar_par_otimo_com_amortizacao(df_baterias, valor_max_armazenamento_baterias, max_throughput_baterias, c.TAXA_DE_JUROS)
display(df_resultados_amortizados.head(10)) # Mostra os 10 primeiros valores  

print("Parcelas em US$")



bateria_a          bateria_b        parcela_a        parcela_b  \
0             Lítio-Íon     Ultracapacitor    75.600.908,54   583.258.741,39   
1  Zinco-Cátodo Híbrido     Ultracapacitor    88.819.230,45   583.234.348,62   
2     Fluxo de Oxidação     Ultracapacitor   103.117.222,67   583.243.081,68   
3         Sódio-Enxofre     Ultracapacitor   117.183.457,75   583.243.928,15   
4           Sódio-Metal     Ultracapacitor   126.636.564,14   583.244.263,54   
5          Chumbo-Ácido     Ultracapacitor   250.065.220,10   583.234.259,68   
6          Chumbo-Ácido          Lítio-Íon             0,00 1.722.621.212,23   
7             Lítio-Íon      Sódio-Enxofre 1.722.621.212,23             0,00   
8             Lítio-Íon  Fluxo de Oxidação 1.722.621.212,23             0,00   
9             Lítio-Íon        Sódio-Metal 1.722.621.212,23             0,00   

             total  
0   658.859.649,93  
1   672.053.579,07  
2   686.360.304,35  
3   700.427.385,90  
4   709.880.827,68  
5   833.299.479,78  
6 1.722.621.212,23  
7 1.722.621.212,23  
8 1.722.621.212,23  
9 1.722.621.212,23

Parcelas em US$


In [22]:
def mostrar_grafico_combinacoes_otimas_amortizadas(df_resultados: pd.DataFrame) -> None:
    """
    Gera e exibe um gráfico de barras horizontais com as combinações ótimas de baterias
    baseado no custo total não amortizado.

    :param df_resultados: DataFrame contendo os resultados das combinações ótimas de baterias.
    """
    melhores_baterias: List[str] = []
    melhores_valores: List[float] = []

    for indice, linha in df_resultados.iterrows():
        if linha['parcela_a'] != 0 and linha['parcela_b'] != 0:
            melhores_baterias.append(linha['bateria_a'] + " + " + linha['bateria_b'])
            melhores_valores.append(linha['total'])
        else:
            if linha['bateria_a'] not in melhores_baterias and linha['parcela_a'] != 0:
                melhores_baterias.append(linha['bateria_a'])
                melhores_valores.append(linha['parcela_a'])
            if linha['bateria_b'] not in melhores_baterias and linha['parcela_b'] != 0:
                melhores_baterias.append(linha['bateria_b'])
                melhores_valores.append(linha['parcela_b'])

    figura = go.Figure()

    figura.add_trace(go.Bar(
        y=melhores_baterias,
        x=melhores_valores,
        name='Valor',
        orientation='h'
    ))

    figura.update_layout(
        title='Combinação Ótima de Baterias - Custo da parcela mensal (com amortização)',
        xaxis_title='Custo Total (US$)',
        yaxis_title='Bateria',
        yaxis=dict(autorange="reversed")
    )

    figura.show()

mostrar_grafico_combinacoes_otimas_amortizadas(df_resultados_amortizados) 


# Cycling Costs

Explicação sobre gráficos 3D

In [23]:
def consumo_combustivel(preco_por_Mft3: float, eficiencia: float) -> float:
    """
    Calcula o custo por megawatt (MW) ao utilizar gás natural como combustível, com base no preço por mil pés cúbicos
    e na eficiência da turbina.

    :param preco_por_Mft3: Preço do gás natural por mil pés cúbicos (Mft^3).
    :param eficiencia: Eficiência da turbina em converter gás natural em energia elétrica.
    :return: O custo por MW de energia gerada.
    """
    # Quanta energia pode ser gerada com 1 m^3 de gás natural, média entre 10.6 e 11.5 kWh, conforme encontrado em https://en.wikipedia.org/wiki/Billion_cubic_metres_of_natural_gas
    potencia_combustivel_em_m3 = 11000 / 3600  # Conversão de Joules para kWh considerando a energia em 1 m^3

    fator_conversao = 28.3168  # Fator de conversão de pés cúbicos para metros cúbicos

    # Converter preço por mil pés cúbicos para preço por metro cúbico
    preco_por_m3 = preco_por_Mft3 / fator_conversao

    preco_por_MW = preco_por_m3 / (eficiencia * potencia_combustivel_em_m3)

    return preco_por_MW


def grafico_tridimensional(potencia_turbina: float, custo_capital: float, custo_inicializacao: float, percentual_uso: float, numero_inicializacoes: int, inflacao_2012: float, inflacao_2019: float, preco_por_Mft3: float, eficiencia_turbina: float, n_turbinas: int) -> float:
    """
    Calcula um valor representando um custo (não especificado na documentação original) com base em várias
    entradas relacionadas ao custo e operação de turbinas de geração de energia.

    :param potencia_turbina: Potência da turbina em MW.
    :param custo_capital: Custo de capital inicial por turbina.
    :param custo_inicializacao: Custo de inicialização para a turbina.
    :param percentual_uso: Percentual de tempo que a turbina está em operação.
    :param numero_inicializacoes: Número de vezes que a turbina é iniciada.
    :param inflacao_2012: Fator de inflação desde 2012.
    :param inflacao_2019: Fator de inflação desde 2019.
    :param preco_por_Mft3: Preço do gás natural por mil pés cúbicos.
    :param eficiencia_turbina: Eficiência da turbina em converter gás natural em energia.
    :param n_turbinas: Número total de turbinas em operação.
    :return: Um valor calculado com base nas variáveis fornecidas.
    """
    return -(((12 * custo_capital * inflacao_2019 / (n_turbinas * potencia_turbina)) + (custo_inicializacao * inflacao_2012 * numero_inicializacoes)) / percentual_uso + consumo_combustivel(preco_por_Mft3, eficiencia_turbina))


def calculo_custo_bat_3d(percentual: float, custo_cap_bat_mw: float, preco_comb: float, eficiencia_turbina: float, numero_s: int) -> float:
    """
    Calcula o custo do ciclo de baterias considerando os seguintes fatores:

    :param percentual: Percentual da capacidade da bateria utilizada.
    :param custo_cap_bat_mw: Custo de capital por MW para baterias.
    :param preco_comb: Preço do combustível.
    :param eficiencia_turbina: Eficiência da turbina.
    :param numero_s: Número de inícios (start-ups) da turbina.

    :return: Custo calculado para o ciclo de bateria.
    """
    return -(12 * custo_cap_bat_mw / (energia_necessaria * percentual)) + consumo_combustivel(preco_comb, eficiencia_turbina) + 0 * numero_s


def calcular_pagamento_mensal(custo_capital_total: float, taxa_juros: float, periodo: int) -> float:
    """
    Calcula o pagamento mensal amortizado para um custo capital total dado.

    :param custo_capital_total: O custo capital total do projeto.
    :param taxa_juros: A taxa de juros anual.
    :param periodo: O período de amortização em meses.

    :return: O valor do pagamento mensal.
    """
    pagamento_mensal = None
    for _, montante, _, _, _ in amortization_schedule(custo_capital_total, taxa_juros, periodo):
        pagamento_mensal = montante
    return pagamento_mensal
